In [1]:
import torch
import torch.nn as nn
import numpy as np
import pandas as pd
from tqdm.auto import tqdm
from sklearn.model_selection import train_test_split
import torch.nn.functional as F
from torch.optim.lr_scheduler import ReduceLROnPlateau
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

c:\Users\Kafka\anaconda3\envs\torch1.1\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
# 定义LSTM模型
class LSTMModel(nn.Module):
    def __init__(self, input_size, hidden_layer_size, output_size, dropout):
        super().__init__()
        self.hidden_layer_size = hidden_layer_size
        self.lstm = nn.LSTM(input_size, hidden_layer_size)
        self.linear = nn.Linear(hidden_layer_size, output_size)
        self.dropout = nn.Dropout(dropout)
        self.hidden_cell = (torch.zeros(1, 1, self.hidden_layer_size, device=device),
                            torch.zeros(1, 1, self.hidden_layer_size, device=device))
        self.batch_norm = nn.BatchNorm1d(input_size)  # 加入归一化层
        
    def forward(self, input_seq):
        input_seq = self.batch_norm(input_seq)  # 归一化
        lstm_out, self.hidden_cell = self.lstm(input_seq.view(len(input_seq), 1, -1), self.hidden_cell)
        lstm_out = self.dropout(lstm_out)
        predictions = self.linear(lstm_out.view(len(input_seq), -1))
        return predictions[-1]

In [3]:
input_size = 8  # 包括空间信息和其他附加特征的总特征数量
output_size = 2  # 经度和纬度
model = LSTMModel(input_size=input_size, hidden_layer_size=100, output_size=output_size,dropout=0.1).to(device)
model.load_state_dict(torch.load('model1.pth'))

IncompatibleKeys(missing_keys=[], unexpected_keys=[])

In [4]:
jump_task = pd.read_csv('../data/jump_task.csv')
jump_task

id                  time  entity_id  traj_id  \
0         355  2013-10-08T08:30:00Z        256       25   
1         356  2013-10-08T08:30:55Z        256       25   
2         357  2013-10-08T08:32:44Z        256       25   
3         358  2013-10-08T08:34:32Z        256       25   
4         359  2013-10-08T08:35:25Z        256       25   
...       ...                   ...        ...      ...   
29380  518325  2013-10-30T22:09:12Z       4954    21997   
29381  518326  2013-10-30T22:09:43Z       4954    21997   
29382  518327  2013-10-30T22:11:26Z       4954    21997   
29383  518328  2013-10-30T22:12:12Z       4954    21997   
29384  518329  2013-10-30T22:13:00Z       4954    21997   

                  coordinates  current_dis   speeds  holidays  
0      [116.324127,39.897049]     0.000000  21.6075         0  
1      [116.327652,39.897018]     0.300751  21.1500         0  
2      [116.330978,39.897041]     0.584521  20.4825         0  
3      [116.336624,39.897305]     1.067123  20.6575         0  
4      [116.341118,39.897537]     1.451388  24.0700         0  
...                       ...          ...      ...       ...  
29380  [116.328094,39.967125]     3.765071  39.0475         0  
29381  [116.330856,39.967224]     4.000737  53.7950         0  
29382  [116.333565,39.967266]     4.232179  44.0800         0  
29383  [116.334488,39.963161]     4.695391  46.4450         0  
29384                     NaN          NaN  21.2225         0  

[29385 rows x 8 columns]

In [5]:
jump_task['time'] = pd.to_datetime(jump_task['time']).astype('int64') / 10**9 * 100 % (1.38 * (10**11))
jump_task

id         time  entity_id  traj_id             coordinates  \
0         355  122100000.0        256       25  [116.324127,39.897049]   
1         356  122105500.0        256       25  [116.327652,39.897018]   
2         357  122116400.0        256       25  [116.330978,39.897041]   
3         358  122127200.0        256       25  [116.336624,39.897305]   
4         359  122132500.0        256       25  [116.341118,39.897537]   
...       ...          ...        ...      ...                     ...   
29380  518325  317095200.0       4954    21997  [116.328094,39.967125]   
29381  518326  317098300.0       4954    21997  [116.330856,39.967224]   
29382  518327  317108600.0       4954    21997  [116.333565,39.967266]   
29383  518328  317113200.0       4954    21997  [116.334488,39.963161]   
29384  518329  317118000.0       4954    21997                     NaN   

       current_dis   speeds  holidays  
0         0.000000  21.6075         0  
1         0.300751  21.1500         0  
2         0.584521  20.4825         0  
3         1.067123  20.6575         0  
4         1.451388  24.0700         0  
...            ...      ...       ...  
29380     3.765071  39.0475         0  
29381     4.000737  53.7950         0  
29382     4.232179  44.0800         0  
29383     4.695391  46.4450         0  
29384          NaN  21.2225         0  

[29385 rows x 8 columns]

In [6]:
jump_task = jump_task[~jump_task['coordinates'].isnull()]
jump_task

id         time  entity_id  traj_id             coordinates  \
0         355  122100000.0        256       25  [116.324127,39.897049]   
1         356  122105500.0        256       25  [116.327652,39.897018]   
2         357  122116400.0        256       25  [116.330978,39.897041]   
3         358  122127200.0        256       25  [116.336624,39.897305]   
4         359  122132500.0        256       25  [116.341118,39.897537]   
...       ...          ...        ...      ...                     ...   
29379  518324  317091600.0       4954    21997   [116.32357,39.966927]   
29380  518325  317095200.0       4954    21997  [116.328094,39.967125]   
29381  518326  317098300.0       4954    21997  [116.330856,39.967224]   
29382  518327  317108600.0       4954    21997  [116.333565,39.967266]   
29383  518328  317113200.0       4954    21997  [116.334488,39.963161]   

       current_dis   speeds  holidays  
0         0.000000  21.6075         0  
1         0.300751  21.1500         0  
2         0.584521  20.4825         0  
3         1.067123  20.6575         0  
4         1.451388  24.0700         0  
...            ...      ...       ...  
29379     3.378877  40.6125         0  
29380     3.765071  39.0475         0  
29381     4.000737  53.7950         0  
29382     4.232179  44.0800         0  
29383     4.695391  46.4450         0  

[27426 rows x 8 columns]

In [7]:
jump_task['x'] = jump_task.apply(lambda row:eval(row['coordinates'])[0],axis=1)
jump_task['y'] = jump_task.apply(lambda row:eval(row['coordinates'])[1],axis=1)
jump_task['x'] = (jump_task['x']-116)*100
jump_task['y'] = (jump_task['y']-39)*100
jump_task = jump_task.drop(columns=['id','coordinates'])
jump_task

c:\Users\Kafka\anaconda3\envs\torch1.1\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.
c:\Users\Kafka\anaconda3\envs\torch1.1\lib\site-packages\ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
c:\Users\Kafka\anaconda3\envs\torch1.1\lib\site-packages\ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_in

time  entity_id  traj_id  current_dis   speeds  holidays  \
0      122100000.0        256       25     0.000000  21.6075         0   
1      122105500.0        256       25     0.300751  21.1500         0   
2      122116400.0        256       25     0.584521  20.4825         0   
3      122127200.0        256       25     1.067123  20.6575         0   
4      122132500.0        256       25     1.451388  24.0700         0   
...            ...        ...      ...          ...      ...       ...   
29379  317091600.0       4954    21997     3.378877  40.6125         0   
29380  317095200.0       4954    21997     3.765071  39.0475         0   
29381  317098300.0       4954    21997     4.000737  53.7950         0   
29382  317108600.0       4954    21997     4.232179  44.0800         0   
29383  317113200.0       4954    21997     4.695391  46.4450         0   

             x        y  
0      32.4127  89.7049  
1      32.7652  89.7018  
2      33.0978  89.7041  
3      33.6624  89.7305  
4      34.1118  89.7537  
...        ...      ...  
29379  32.3570  96.6927  
29380  32.8094  96.7125  
29381  33.0856  96.7224  
29382  33.3565  96.7266  
29383  33.4488  96.3161  

[27426 rows x 8 columns]

In [ ]:
# jump_task['x'] = jump_task.apply(lambda row:eval(row['coordinates'])[0],axis=1)
# jump_task['y'] = jump_task.apply(lambda row:eval(row['coordinates'])[1],axis=1)

# jump_task = jump_task.drop(columns=['id','coordinates'])
# jump_task

In [8]:
tensors_list = []

for start in range(0, len(jump_task), 14):
    end = start + 14
    # 选取14行数据
    subset = jump_task.iloc[start:end]
    tensor = torch.tensor(subset.values, dtype=torch.float32)
    tensors_list.append(tensor)

tensors_list

[tensor([[1.2210e+08, 2.5600e+02, 2.5000e+01, 0.0000e+00, 2.1608e+01, 0.0000e+00,
          3.2413e+01, 8.9705e+01],
         [1.2211e+08, 2.5600e+02, 2.5000e+01, 3.0075e-01, 2.1150e+01, 0.0000e+00,
          3.2765e+01, 8.9702e+01],
         [1.2212e+08, 2.5600e+02, 2.5000e+01, 5.8452e-01, 2.0483e+01, 0.0000e+00,
          3.3098e+01, 8.9704e+01],
         [1.2213e+08, 2.5600e+02, 2.5000e+01, 1.0671e+00, 2.0657e+01, 0.0000e+00,
          3.3662e+01, 8.9730e+01],
         [1.2213e+08, 2.5600e+02, 2.5000e+01, 1.4514e+00, 2.4070e+01, 0.0000e+00,
          3.4112e+01, 8.9754e+01],
         [1.2214e+08, 2.5600e+02, 2.5000e+01, 1.8626e+00, 2.0655e+01, 0.0000e+00,
          3.4592e+01, 8.9782e+01],
         [1.2214e+08, 2.5600e+02, 2.5000e+01, 2.4368e+00, 1.8120e+01, 0.0000e+00,
          3.5265e+01, 8.9788e+01],
         [1.2216e+08, 2.5600e+02, 2.5000e+01, 2.7076e+00, 2.0548e+01, 0.0000e+00,
          3.5574e+01, 8.9837e+01],
         [1.2218e+08, 2.5600e+02, 2.5000e+01, 2.9933e+00, 2.2760

In [9]:
outputs = []
model.eval()
# 进行预测
for t in tensors_list:
    print(t)
    with torch.no_grad():
        output = model(t.to(device))
        outputs.append(output)
outputs

tensor([[1.2210e+08, 2.5600e+02, 2.5000e+01, 0.0000e+00, 2.1608e+01, 0.0000e+00,
         3.2413e+01, 8.9705e+01],
        [1.2211e+08, 2.5600e+02, 2.5000e+01, 3.0075e-01, 2.1150e+01, 0.0000e+00,
         3.2765e+01, 8.9702e+01],
        [1.2212e+08, 2.5600e+02, 2.5000e+01, 5.8452e-01, 2.0483e+01, 0.0000e+00,
         3.3098e+01, 8.9704e+01],
        [1.2213e+08, 2.5600e+02, 2.5000e+01, 1.0671e+00, 2.0657e+01, 0.0000e+00,
         3.3662e+01, 8.9730e+01],
        [1.2213e+08, 2.5600e+02, 2.5000e+01, 1.4514e+00, 2.4070e+01, 0.0000e+00,
         3.4112e+01, 8.9754e+01],
        [1.2214e+08, 2.5600e+02, 2.5000e+01, 1.8626e+00, 2.0655e+01, 0.0000e+00,
         3.4592e+01, 8.9782e+01],
        [1.2214e+08, 2.5600e+02, 2.5000e+01, 2.4368e+00, 1.8120e+01, 0.0000e+00,
         3.5265e+01, 8.9788e+01],
        [1.2216e+08, 2.5600e+02, 2.5000e+01, 2.7076e+00, 2.0548e+01, 0.0000e+00,
         3.5574e+01, 8.9837e+01],
        [1.2218e+08, 2.5600e+02, 2.5000e+01, 2.9933e+00, 2.2760e+01, 0.0000e+00,

[tensor([35.2402, 89.8256], device='cuda:0'),
 tensor([35.2402, 89.8256], device='cuda:0'),
 tensor([35.2402, 89.8256], device='cuda:0'),
 tensor([34.2548, 89.1932], device='cuda:0'),
 tensor([34.8535, 89.4137], device='cuda:0'),
 tensor([34.2548, 89.1932], device='cuda:0'),
 tensor([34.2548, 89.1932], device='cuda:0'),
 tensor([34.2548, 89.1932], device='cuda:0'),
 tensor([34.2548, 89.1932], device='cuda:0'),
 tensor([34.2548, 89.1932], device='cuda:0'),
 tensor([34.2548, 89.1932], device='cuda:0'),
 tensor([34.2548, 89.1932], device='cuda:0'),
 tensor([34.2548, 89.1932], device='cuda:0'),
 tensor([34.2548, 89.1932], device='cuda:0'),
 tensor([34.2548, 89.1932], device='cuda:0'),
 tensor([34.2548, 89.1932], device='cuda:0'),
 tensor([34.2548, 89.1932], device='cuda:0'),
 tensor([34.2548, 89.1932], device='cuda:0'),
 tensor([34.2548, 89.1932], device='cuda:0'),
 tensor([34.2548, 89.1932], device='cuda:0'),
 tensor([34.2548, 89.1932], device='cuda:0'),
 tensor([34.2548, 89.1932], device

In [10]:
jump_task_old = pd.read_csv('../data/jump_task.csv')
jump_task_old

id                  time  entity_id  traj_id  \
0         355  2013-10-08T08:30:00Z        256       25   
1         356  2013-10-08T08:30:55Z        256       25   
2         357  2013-10-08T08:32:44Z        256       25   
3         358  2013-10-08T08:34:32Z        256       25   
4         359  2013-10-08T08:35:25Z        256       25   
...       ...                   ...        ...      ...   
29380  518325  2013-10-30T22:09:12Z       4954    21997   
29381  518326  2013-10-30T22:09:43Z       4954    21997   
29382  518327  2013-10-30T22:11:26Z       4954    21997   
29383  518328  2013-10-30T22:12:12Z       4954    21997   
29384  518329  2013-10-30T22:13:00Z       4954    21997   

                  coordinates  current_dis   speeds  holidays  
0      [116.324127,39.897049]     0.000000  21.6075         0  
1      [116.327652,39.897018]     0.300751  21.1500         0  
2      [116.330978,39.897041]     0.584521  20.4825         0  
3      [116.336624,39.897305]     1.067123  20.6575         0  
4      [116.341118,39.897537]     1.451388  24.0700         0  
...                       ...          ...      ...       ...  
29380  [116.328094,39.967125]     3.765071  39.0475         0  
29381  [116.330856,39.967224]     4.000737  53.7950         0  
29382  [116.333565,39.967266]     4.232179  44.0800         0  
29383  [116.334488,39.963161]     4.695391  46.4450         0  
29384                     NaN          NaN  21.2225         0  

[29385 rows x 8 columns]

In [11]:
jump_task_old.head(30)

id                  time  entity_id  traj_id             coordinates  \
0   355  2013-10-08T08:30:00Z        256       25  [116.324127,39.897049]   
1   356  2013-10-08T08:30:55Z        256       25  [116.327652,39.897018]   
2   357  2013-10-08T08:32:44Z        256       25  [116.330978,39.897041]   
3   358  2013-10-08T08:34:32Z        256       25  [116.336624,39.897305]   
4   359  2013-10-08T08:35:25Z        256       25  [116.341118,39.897537]   
5   360  2013-10-08T08:36:20Z        256       25   [116.345924,39.89782]   
6   361  2013-10-08T08:37:11Z        256       25  [116.352654,39.897881]   
7   362  2013-10-08T08:40:28Z        256       25  [116.355743,39.898369]   
8   363  2013-10-08T08:44:05Z        256       25  [116.358871,39.899197]   
9   364  2013-10-08T08:45:53Z        256       25  [116.361748,39.899303]   
10  365  2013-10-08T08:46:47Z        256       25  [116.364128,39.899414]   
11  366  2013-10-08T08:48:37Z        256       25  [116.374619,39.899754]   
12  367  2013-10-08T08:49:31Z        256       25  [116.380623,39.899956]   
13  368  2013-10-08T08:51:18Z        256       25  [116.387314,39.900158]   
14  369  2013-10-08T08:52:13Z        256       25                     NaN   
15  547  2013-10-08T08:30:00Z        257       40   [116.408173,39.79324]   
16  548  2013-10-08T08:30:36Z        257       40  [116.411362,39.793404]   
17  549  2013-10-08T08:31:12Z        257       40  [116.414215,39.793545]   
18  550  2013-10-08T08:31:36Z        257       40  [116.416885,39.793655]   
19  551  2013-10-08T08:32:24Z        257       40  [116.419693,39.793449]   
20  552  2013-10-08T08:33:17Z        257       40   [116.420586,39.78878]   
21  553  2013-10-08T08:35:13Z        257       40  [116.421707,39.786469]   
22  554  2013-10-08T08:35:36Z        257       40  [116.424622,39.784592]   
23  555  2013-10-08T08:37:13Z        257       40  [116.426712,39.783386]   
24  556  2013-10-08T08:37:48Z        257       40  [116.428291,39.785343]   
25  557  2013-10-08T08:38:36Z        257       40  [116.430511,39.788353]   
26  558  2013-10-08T08:39:36Z        257       40  [116.430969,39.790245]   
27  559  2013-10-08T08:40:00Z        257       40  [116.430298,39.793922]   
28  560  2013-10-08T08:40:13Z        257       40  [116.430077,39.795883]   
29  561  2013-10-08T08:40:24Z        257       40                     NaN   

    current_dis   speeds  holidays  
0      0.000000  21.6075         0  
1      0.300751  21.1500         0  
2      0.584521  20.4825         0  
3      1.067123  20.6575         0  
4      1.451388  24.0700         0  
5      1.862608  20.6550         0  
6      2.436804  18.1200         0  
7      2.707566  20.5475         0  
8      2.993256  22.7600         0  
9      3.238989  27.7250         0  
10     3.442404  19.6500         0  
11     4.338202  19.0550         0  
12     4.850897  34.7700         0  
13     5.422169  40.9575         0  
14          NaN  22.6325         0  
15     0.000000  26.4025         0  
16     0.273088  11.5600         0  
17     0.517418  21.9625         0  
18     0.745877  20.0150         0  
19     0.995370  33.1400         0  
20     1.520256  25.2225         0  
21     1.802695  17.2050         0  
22     2.127683  33.5150         0  
23     2.352990  26.2625         0  
24     2.619818  52.2200         0  
25     3.008097  40.7275         0  
26     3.291492  32.9175         0  
27     3.704447  69.2825         0  
28     3.923330  58.5675         0  
29          NaN  55.8975         0

In [12]:
j = 0
for i in range(14, len(jump_task_old), 15):
    tmp = []
    tmp.append(round(outputs[j][0].item() / 100 + 116,6))
    tmp.append(round(outputs[j][1].item() / 100 + 39,6))
    j+=1
    jump_task_old.loc[i,'coordinates'] = str(tmp)
jump_task_old

id                  time  entity_id  traj_id  \
0         355  2013-10-08T08:30:00Z        256       25   
1         356  2013-10-08T08:30:55Z        256       25   
2         357  2013-10-08T08:32:44Z        256       25   
3         358  2013-10-08T08:34:32Z        256       25   
4         359  2013-10-08T08:35:25Z        256       25   
...       ...                   ...        ...      ...   
29380  518325  2013-10-30T22:09:12Z       4954    21997   
29381  518326  2013-10-30T22:09:43Z       4954    21997   
29382  518327  2013-10-30T22:11:26Z       4954    21997   
29383  518328  2013-10-30T22:12:12Z       4954    21997   
29384  518329  2013-10-30T22:13:00Z       4954    21997   

                   coordinates  current_dis   speeds  holidays  
0       [116.324127,39.897049]     0.000000  21.6075         0  
1       [116.327652,39.897018]     0.300751  21.1500         0  
2       [116.330978,39.897041]     0.584521  20.4825         0  
3       [116.336624,39.897305]     1.067123  20.6575         0  
4       [116.341118,39.897537]     1.451388  24.0700         0  
...                        ...          ...      ...       ...  
29380   [116.328094,39.967125]     3.765071  39.0475         0  
29381   [116.330856,39.967224]     4.000737  53.7950         0  
29382   [116.333565,39.967266]     4.232179  44.0800         0  
29383   [116.334488,39.963161]     4.695391  46.4450         0  
29384  [116.369259, 39.944316]          NaN  21.2225         0  

[29385 rows x 8 columns]

In [13]:
jump_task_old.to_csv('jump_task_finished2.csv',index=False)